In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pymc3 as pm
import patsy
import os, sys
from sklearn.cluster import KMeans
from sklearn.cross_validation import train_test_split
from PriceHistory import PriceHistory
from tickers import tickers
from tqdm import tqdm_notebook
from models import EveryStock, VolumeCategorized
%matplotlib inline
pd.set_option('max_columns', 1000)

WARNING (theano.sandbox.cuda): The cuda backend is deprecated and will be removed in the next release (v0.10).  Please switch to the gpuarray backend. You can get more information about how to switch at this URL:
 https://github.com/Theano/Theano/wiki/Converting-to-the-new-gpu-back-end%28gpuarray%29

Using gpu device 0: GeForce GTX 980 (CNMeM is disabled, cuDNN not available)
/home/ben/anaconda3/envs/py35/lib/python3.5/site-packages/sklearn/cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [2]:
es = EveryStock('momentum')

In [3]:
es.X_train.shape

(934453, 7)

In [4]:
es.train()

100%|██████████| 300/300 [62:43:50<00:00, 751.57s/it]/home/ben/anaconda3/envs/py35/lib/python3.5/site-packages/pymc3/step_methods/hmc/nuts.py:429: UserWarning: Chain 0 contains only 100 samples.
  % (self._chain_id, n))
/home/ben/anaconda3/envs/py35/lib/python3.5/site-packages/pymc3/step_methods/hmc/nuts.py:451: UserWarning: The acceptance probability in chain 0 does not match the target. It is 0.886509135684, but should be close to 0.8. Try to increase the number of tuning steps.
  % (self._chain_id, mean_accept, target_accept))



In [6]:
es.print_output()

{'a_security': {'ADSK': array([-0.18890865,  0.70954114,  0.85326874, -0.56360859,  1.17923629,
       -0.50370771,  1.52977479,  1.57770109,  0.01498187,  0.7371161 ,
        0.73569101,  0.77996361,  0.49872199,  0.70909464, -0.3023555 ,
        0.32094353,  0.89257401,  0.19313402,  0.77408451, -0.51954103,
        1.69383192,  0.24427047,  0.66671777,  0.41162422,  0.40566751,
        0.31877854,  0.72789317,  0.00450734,  0.53973198,  0.28696147,
        0.27364895, -0.5588311 ,  1.27677417, -0.06240773,  0.98905885,
        0.46653348, -0.13529494,  1.36812913, -0.29852298,  1.35779762,
       -0.29834342,  0.45771179,  1.04671252,  0.82109809,  1.14263988,
        0.36029387,  0.71421921,  0.17554627,  0.26100156,  0.38578105,
        0.42664295,  0.7197302 , -0.08235826,  1.04898381, -0.28538102,
        0.7933569 ,  0.75054818, -0.01805607, -0.14873745,  0.16745631,
        1.19396818, -0.65800303,  0.06312115,  1.3723985 ,  0.2679204 ,
        0.29246688,  0.75812864,  0.5115

In [8]:
es.predict()

AttributeError: 'DataFrame' object has no attribute 'progress_apply'

In [38]:

dists = {}
for v in es.trace.varnames:
    dists[v] = {}
    _a = es.trace.get_values(v)
    if len(_a.shape) > 1:
        for i, d in enumerate(_a.transpose()):
            dists[v][es.sec_category_map[i]] = d[50:]
    else:
        dists[v]['sec'] = _a[50:]
print(dists.keys())


dict_keys(['a_security', 'b_security_interval__', 'a_category_sd', 'b_security', 'a_category_sd_log__', 'a_category_mu'])


In [39]:
del dists['b_security_interval__']
del dists['a_category_sd']
del dists['a_category_sd_log__']
del dists['a_category_mu']

In [40]:
dists['a_security']['A'].shape

(50,)

In [16]:
es_val = EveryStock('value')

In [17]:
es_val.train()

100%|██████████| 300/300 [22:43:04<00:00, 187.77s/it]/home/ben/anaconda3/envs/py35/lib/python3.5/site-packages/pymc3/step_methods/hmc/nuts.py:429: UserWarning: Chain 0 contains only 100 samples.
  % (self._chain_id, n))
/home/ben/anaconda3/envs/py35/lib/python3.5/site-packages/pymc3/step_methods/hmc/nuts.py:451: UserWarning: The acceptance probability in chain 0 does not match the target. It is 0.880428247864, but should be close to 0.8. Try to increase the number of tuning steps.
  % (self._chain_id, mean_accept, target_accept))



In [18]:
val_dists = es_val.dists

AttributeError: 'EveryStock' object has no attribute 'dists'

In [41]:
val_dists = {}
for v in es_val.trace.varnames:
    val_dists[v] = {}
    _a = es_val.trace.get_values(v)
    if len(_a.shape) > 1:
        for i, d in enumerate(_a.transpose()):
            val_dists[v][es.sec_category_map[i]] = d[50:]
    else:
        val_dists[v]['sec'] = _a[50:]

In [42]:
del val_dists['b_security_interval__']
del val_dists['a_category_sd']
del val_dists['a_category_sd_log__']
del val_dists['a_category_mu']

In [26]:
val_dists

{'a_security': {'A': array([-0.35125697, -0.62173724, -0.24692322, -0.5349263 , -0.38620108,
         -0.48431531, -0.4617261 , -0.35876098, -0.46516311, -0.46491343,
         -0.27328306, -0.51069236, -0.09020181, -0.57749826, -0.68018639,
         -0.40110162, -0.09187519, -0.67734832, -0.23023142, -0.31669706,
         -0.10163003, -0.459032  , -0.15688948, -0.25065267, -0.51132959,
         -0.18713298, -0.47618401, -0.16310625, -0.43963411, -0.22971839,
         -0.46084768, -0.38003674, -0.20563307, -0.45515803, -0.71834648,
         -0.3805691 , -0.24459405, -0.12842716, -0.68163854,  0.01299413,
         -0.51610804, -0.3230598 , -0.32290417, -0.62613755, -0.17972551,
         -0.41223252, -0.34713709, -0.39266786, -0.31632558, -0.45393258,
         -0.33196986, -0.16051805, -0.58756435, -0.14202686, -0.4957374 ,
         -0.51062638, -0.15315798, -0.58074129, -0.02750821, -0.55580473,
         -0.42535493, -0.53057456, -0.20723364, -0.50462341, -0.20635617,
         -0.4128816

In [43]:
dists=dict(mom=dists, val=val_dists)

In [44]:
dists

{'mom': {'a_security': {'A': array([ 0.85638875,  1.5021975 ,  0.94939691,  1.08490515,  2.49604511,
           0.31424323,  0.33331642,  2.68476176,  0.83820802,  0.49233076,
           1.66514099,  0.42962557,  2.16006088,  2.3099184 ,  0.2172752 ,
           2.9057126 ,  0.30769715,  2.44441295,  1.72337687,  0.88688475,
           1.66814864,  3.21921039,  2.35993552,  1.59779084,  0.97944784,
           1.70426774,  0.99991339,  2.00172353,  2.37177205,  0.79069114,
           1.2680521 ,  1.13683236,  2.67241502,  2.09270382,  1.22285593,
           1.18140066,  0.95390761,  0.67879373,  1.49292028,  1.36192107,
           1.59246445,  1.11259544,  1.838328  ,  1.38042092,  1.403355  ,
           1.54102468, -0.48918515,  2.98736906,  0.16800076,  1.59776139], dtype=float32),
   'AAL': array([-0.90022135,  0.47514156,  1.69852293,  0.55827957, -0.11279797,
           0.41082293,  0.42977569,  0.78897995, -0.49032518,  0.03424196,
          -0.749017  , -0.35229385, -0.3105233 , -